# Определение стоимости автомобилей

Сервис по продаже автомобилей с пробегом «Не бит, не крашен» разрабатывает приложение для привлечения новых клиентов. В нём можно быстро узнать рыночную стоимость своего автомобиля. В нашем распоряжении исторические данные: технические характеристики, комплектации и цены автомобилей. Нам нужно построить модель для определения стоимости. 

Заказчику важны:

- качество предсказания;
- скорость предсказания;
- время обучения.

### План проведения работы

Основные шаги:

    Загрузим данные.
    Изучим данные. Заполним пропущенные значения и обработаем аномалии в столбцах. Если среди признаков имеются неинформативные, удалим их.
    Подготовим выборки для обучения моделей.
    Обучим разные модели, одну линейную — LinearRegression, одну ансамблевую — RandomForest и две бустинг модели — LightGBM, CatBoost. Для каждой модели попробуем разные гиперпараметры.
    Проанализируем время обучения, время предсказания и качество моделей.
    Опираясь на критерии заказчика, выберем лучшую модель, проверим её качество на тестовой выборке.

Примечания:

    Для оценки качества моделей применим метрику RMSE.
    Значение метрики RMSE должно быть меньше 2500.

### Описание данных

Признаки

    DateCrawled — дата скачивания анкеты из базы
    VehicleType — тип автомобильного кузова
    RegistrationYear — год регистрации автомобиля
    Gearbox — тип коробки передач
    Power — мощность (л. с.)
    Model — модель автомобиля
    Kilometer — пробег (км)
    RegistrationMonth — месяц регистрации автомобиля
    FuelType — тип топлива
    Brand — марка автомобиля
    NotRepaired — была машина в ремонте или нет
    DateCreated — дата создания анкеты
    NumberOfPictures — количество фотографий автомобиля
    PostalCode — почтовый индекс владельца анкеты (пользователя)
    LastSeen — дата последней активности пользователя

Целевой признак

    Price — цена (евро)

## Подготовка данных

Установим дополнительную библиотеку pandas_profiling для EDA и библиотеку LightGBM.

In [1]:
!pip install pandas_profiling -q

In [2]:
!pip install lightgbm -q

Импортируем необходимые библиотеки.

In [3]:
import os
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt

import pandas_profiling

from sklearn.model_selection import train_test_split

from sklearn.dummy import DummyRegressor

from sklearn.metrics import mean_squared_error, make_scorer

from sklearn.preprocessing import OneHotEncoder, OrdinalEncoder, StandardScaler, LabelEncoder
from sklearn.compose import make_column_transformer, make_column_selector

from sklearn.pipeline import make_pipeline
from sklearn.model_selection import GridSearchCV

from sklearn.linear_model import LinearRegression
from sklearn.ensemble import RandomForestRegressor, GradientBoostingRegressor

import lightgbm as lgb

from catboost import CatBoostRegressor

Объявим глобальные переменные.

In [4]:
SEED = 314159

Загрузим данные.

In [5]:
if os.path.exists('autos.csv'):
    df = pd.read_csv('autos.csv')
else:
    df = pd.read_csv('/datasets/autos.csv')

Сделаем первичный осмотр.

In [6]:
df.info()
display(df.head())
display(df.describe().transpose())

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 354369 entries, 0 to 354368
Data columns (total 16 columns):
 #   Column             Non-Null Count   Dtype 
---  ------             --------------   ----- 
 0   DateCrawled        354369 non-null  object
 1   Price              354369 non-null  int64 
 2   VehicleType        316879 non-null  object
 3   RegistrationYear   354369 non-null  int64 
 4   Gearbox            334536 non-null  object
 5   Power              354369 non-null  int64 
 6   Model              334664 non-null  object
 7   Kilometer          354369 non-null  int64 
 8   RegistrationMonth  354369 non-null  int64 
 9   FuelType           321474 non-null  object
 10  Brand              354369 non-null  object
 11  NotRepaired        283215 non-null  object
 12  DateCreated        354369 non-null  object
 13  NumberOfPictures   354369 non-null  int64 
 14  PostalCode         354369 non-null  int64 
 15  LastSeen           354369 non-null  object
dtypes: int64(7), object(

DateCrawled  Price VehicleType  RegistrationYear Gearbox  Power  \
0  2016-03-24 11:52:17    480         NaN              1993  manual      0   
1  2016-03-24 10:58:45  18300       coupe              2011  manual    190   
2  2016-03-14 12:52:21   9800         suv              2004    auto    163   
3  2016-03-17 16:54:04   1500       small              2001  manual     75   
4  2016-03-31 17:25:20   3600       small              2008  manual     69   

   Model  Kilometer  RegistrationMonth  FuelType       Brand NotRepaired  \
0   golf     150000                  0    petrol  volkswagen         NaN   
1    NaN     125000                  5  gasoline        audi         yes   
2  grand     125000                  8  gasoline        jeep         NaN   
3   golf     150000                  6    petrol  volkswagen          no   
4  fabia      90000                  7  gasoline       skoda          no   

           DateCreated  NumberOfPictures  PostalCode             LastSeen  
0  2016-03-24 00:00:00                 0       70435  2016-04-07 03:16:57  
1  2016-03-24 00:00:00                 0       66954  2016-04-07 01:46:50  
2  2016-03-14 00:00:00                 0       90480  2016-04-05 12:47:46  
3  2016-03-17 00:00:00                 0       91074  2016-03-17 17:40:17  
4  2016-03-31 00:00:00                 0       60437  2016-04-06 10:17:21

count           mean           std     min       25%  \
Price              354369.0    4416.656776   4514.158514     0.0    1050.0   
RegistrationYear   354369.0    2004.234448     90.227958  1000.0    1999.0   
Power              354369.0     110.094337    189.850405     0.0      69.0   
Kilometer          354369.0  128211.172535  37905.341530  5000.0  125000.0   
RegistrationMonth  354369.0       5.714645      3.726421     0.0       3.0   
NumberOfPictures   354369.0       0.000000      0.000000     0.0       0.0   
PostalCode         354369.0   50508.689087  25783.096248  1067.0   30165.0   

                        50%       75%       max  
Price                2700.0    6400.0   20000.0  
RegistrationYear     2003.0    2008.0    9999.0  
Power                 105.0     143.0   20000.0  
Kilometer          150000.0  150000.0  150000.0  
RegistrationMonth       6.0       9.0      12.0  
NumberOfPictures        0.0       0.0       0.0  
PostalCode          49413.0   71083.0   99998.0

Проверим общее количество дубликатов до сброса неинформативных столбцов.

In [7]:
df.duplicated().value_counts()

False    354365
True          4
dtype: int64

In [8]:
df.drop_duplicates(inplace=True)

Удалим неинформативные столбцы:

    DateCrawled, RegistrationMonth, DateCreated, PostalCode, LastSeen, NumberOfPictures

In [9]:
df.drop(columns=['DateCrawled', 'RegistrationMonth', 'DateCreated', 'PostalCode', 'LastSeen', 'NumberOfPictures'],
        inplace=True,
        errors='ignore')

Переименуем оставшиеся столбцы в соответствии с рекомендациями PEP 8.

In [10]:
df.rename(columns={'Price':'price', 'VehicleType':'vehicle_type',
                   'RegistrationYear':'registration_year', 'Gearbox':'gearbox',
                   'Power':'power', 'Model':'model',
                   'Kilometer':'kilometer', 'FuelType':'fuel_type',
                   'Brand':'brand', 'NotRepaired':'not_repaired'},
         inplace=True)

Для просмотра пропусков и дубликатов воспользуемся библиотекой **pandas profiling**.

In [11]:
df.profile_report()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Видно большое количество пропусков и дубликатов. Однако, если посмотреть на данные до удаления неинформативных столбцов - там дубликатов почти нет.

Разберёмся с аномалиями. В столбце с ценами присутствуют нули. Пользователи не ввели стоимость автомобиля, т.к. это целевой признак - заполнять не станем, чтобы не искажать результаты работы модели. Сбросим.

Так же зададимся некой минимальной стоимостью, ниже которой люди устанавливают цену только если хотят повысить место выдачи в поиске. Пусть будет 5 персентиль.

In [12]:
df.drop(df[df['price'] == 0].index, inplace=True)
df.drop(df[df['price'] < df.price.quantile(.05)].index, inplace=True)

В столбце с типом автомобиля почти 37,5 тысяч пропусков. Можно заполнить категорией `other`, но тогда мы поднимем эту категорию сразу до 4го места по частоте и сделаем данные сильно "шумными", лучше удалить.

In [13]:
df.dropna(subset=['vehicle_type'], inplace=True)

В столбце `registration_year` удалим значения ниже 1886 (первый автомобиль) и выше 2016 года (максимальный год размещения объявлений).

In [14]:
df.drop(df[df['registration_year'] < 1886].index, inplace=True)
df.drop(df[df['registration_year'] > 2016].index, inplace=True)

В столбце с типом коробки передач много пропусков, но в автоматическом режиме выяснить и заполнить невозможно. Лучше сбросить эти строки.

In [15]:
df.dropna(subset=['gearbox'], inplace=True)

В столбце мощности также есть большое количество нулей и нереальных значений. Зададим диапазон от 50 до 2000 лошадей.

In [16]:
df.drop(df[df['power'] < 50].index, inplace=True)
df.drop(df[df['power'] > 2000].index, inplace=True)

Пропуски в столбце с обозначением моделей и в столбце `fuel_type` также сбросим.

In [17]:
df.dropna(subset=['model'], inplace=True)
df.dropna(subset=['fuel_type'], inplace=True)

Проверим уникальные значения в столбце `fuel_type`.

In [18]:
df.brand.unique()

array(['jeep', 'volkswagen', 'skoda', 'bmw', 'peugeot', 'ford', 'mazda',
       'nissan', 'renault', 'mercedes_benz', 'seat', 'honda', 'fiat',
       'mini', 'smart', 'audi', 'subaru', 'volvo', 'mitsubishi', 'opel',
       'alfa_romeo', 'kia', 'hyundai', 'lancia', 'citroen', 'toyota',
       'chevrolet', 'dacia', 'suzuki', 'daihatsu', 'chrysler', 'jaguar',
       'rover', 'porsche', 'saab', 'daewoo', 'land_rover', 'lada',
       'trabant'], dtype=object)

Пропуски в столбце `not_repaired` заполним значением `unknown`.

*feature-request для frontend - сделать поле обязательным для заполнения, подойдёт radio-button.*

In [19]:
df.loc[df['not_repaired'].isna(), 'not_repaired'] = 'unknown'
df.reset_index(drop=True, inplace=True)

Проверим ещё раз получившийся датасет.

In [20]:
df.profile_report()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

### Вывод

Мы загрузили данные и провели их предобработку.

Переименовали столбцы и избавились от неинформативных. Убрали строки с пустыми значениями, избавились от аномалий и частично заполнили пропуски.

До сокращения столбцов мы избавились от дубликатов, но после - появилось большое их количество. Это связано с тем что убрав уникальную, но бесполезную для нас информацию, мы получили целые группы автомобилей со схожими основными характеристиками. Поскольку данные автомобили реальны, оставим их на месте.

По данным отчётов мы видим сильную прямую зависимость цены он года регистрации и мощности двигателя и обратную зависимость от пробега.

## Обучение моделей

Разделим данные на обучающие и тестовые для features(X) и target(y).

In [21]:
X = df.drop(['price'], axis=1)
y = df['price']

X, X_test, y, y_test = train_test_split(
    X, y,
    test_size=.2,
    random_state=SEED
)

Проверим корерктность разделения на выборки.

In [22]:
print(f'Доля тренировочных признаков: {X.shape[0]/df.shape[0]:.2f}')
print(f'Доля тренировочных целей: {y.shape[0]/df.shape[0]:.2f}')
print(f'Доля тестовых признаков: {X_test.shape[0]/df.shape[0]:.2f}')
print(f'Доля тестовых целей: {y_test.shape[0]/df.shape[0]:.2f}')

Доля тренировочных признаков: 0.80
Доля тренировочных целей: 0.80
Доля тестовых признаков: 0.20
Доля тестовых целей: 0.20


Для начала зададим baseline, найдём результаты для константной модели.

In [23]:
model_dc = DummyRegressor(strategy='median')

In [24]:
%time model_dc.fit(X, y)

CPU times: user 3.38 ms, sys: 0 ns, total: 3.38 ms
Wall time: 3.11 ms


DummyRegressor(strategy='median')

In [25]:
%time prediction_dc = model_dc.predict(X_test)

CPU times: user 642 µs, sys: 102 µs, total: 744 µs
Wall time: 520 µs


In [26]:
rmse_dc = int(mean_squared_error(y_test, prediction_dc, squared=False))
print(f'Метрика RMSE на константной модели составила {rmse_dc} евро.')

Метрика RMSE на константной модели составила 4950 евро.


Занёсем результаты в словарь для последующего сравнения.

In [27]:
results_table = {
    'DummyRegressor':[3.0, 0.5, 4950]
}

Результаты далеки от приемлемых значений.

Приступим к исследованию моделей машинного обучения.

### Модель LinearRegression

Создадим трансформер для различных колонок, в случае с "линейными" моделями к категориальным применим OHE, к числовым - StandardScaler.

In [28]:
linear_transformer = make_column_transformer(
    (
        OneHotEncoder(
            dtype='uint8',
            handle_unknown='ignore'
        ), make_column_selector(dtype_include='object')
    ),
    (
        StandardScaler(
        ), make_column_selector(dtype_include='number')
    ),
    remainder='passthrough'
)

Соберём pipeline для линейной регрессии.

In [29]:
pipe_lr = make_pipeline(
    linear_transformer,
    LinearRegression(
        n_jobs=-1
    )
)

Зададим сетку параметров и создадим estimator.

In [30]:
param_grid = {
    'linearregression__normalize':[False, True]
}

gs_lr = GridSearchCV(
    pipe_lr,
    param_grid,
    scoring='neg_root_mean_squared_error',
    n_jobs=-1,
    verbose=1
)

Проведём обучение.

In [31]:
%time gs_lr.fit(X, y)

Fitting 5 folds for each of 2 candidates, totalling 10 fits
CPU times: user 53.3 s, sys: 1min 26s, total: 2min 19s
Wall time: 2min 19s


GridSearchCV(estimator=Pipeline(steps=[('columntransformer',
                                        ColumnTransformer(remainder='passthrough',
                                                          transformers=[('onehotencoder',
                                                                         OneHotEncoder(dtype='uint8',
                                                                                       handle_unknown='ignore'),
                                                                         <sklearn.compose._column_transformer.make_column_selector object at 0x7f601e8a6760>),
                                                                        ('standardscaler',
                                                                         StandardScaler(),
                                                                         <sklearn.compose._column_transformer.make_column_selector object at 0x7f601e8a6b20>)])),
                                       ('linearr

Посмотрим на результаты.

In [32]:
pd.DataFrame(gs_lr.cv_results_)[[
    'param_linearregression__normalize',
    'mean_test_score', 'rank_test_score'
]]

param_linearregression__normalize  mean_test_score  rank_test_score
0                             False     -2553.288151                1
1                              True     -2553.298728                2

Занесём результаты в итоговую таблицу.

In [33]:
results = pd.DataFrame(gs_lr.cv_results_)

results_table[gs_lr.best_estimator_.named_steps[gs_lr.best_estimator_.steps[1][0]].__class__.__name__] = [
    results[results['rank_test_score'] == 1]['mean_fit_time'].values[0],
    results[results['rank_test_score'] == 1]['mean_score_time'].values[0],
    abs(results[results['rank_test_score'] == 1]['mean_test_score'].values[0])
]

Проверим ансамблевые модели.

### Модель RandomForestRegressor

Создадим трансформер для различных колонок, в случае с "деревянными моделями" к категориальным применим OE, числовые оставим как есть.

In [34]:
ensemble_transformer = make_column_transformer(
    (
        OrdinalEncoder(
            dtype='int16',
            handle_unknown='use_encoded_value',
            unknown_value=-1
        ), make_column_selector(dtype_include='object')
    ),
    remainder='passthrough'
)

Создадим pipeline.

In [35]:
pipe_rf = make_pipeline(
    ensemble_transformer,
    RandomForestRegressor(
        oob_score=True,
        n_jobs=-1,
        verbose=0
    )
)

Зададим сетку параметров и создадим estimator.

In [36]:
param_grid = {
    'randomforestregressor__max_depth':np.arange(5, 16, 5)
}

gs_rf = GridSearchCV(
    pipe_rf,
    param_grid,
    scoring='neg_root_mean_squared_error',
    n_jobs=-1,
    verbose=1
)

Проведём обучение с кросс-валидацией выбранного оценщика.

In [37]:
%time gs_rf.fit(X, y)

Fitting 5 folds for each of 3 candidates, totalling 15 fits
CPU times: user 6min 5s, sys: 0 ns, total: 6min 5s
Wall time: 6min 5s


GridSearchCV(estimator=Pipeline(steps=[('columntransformer',
                                        ColumnTransformer(remainder='passthrough',
                                                          transformers=[('ordinalencoder',
                                                                         OrdinalEncoder(dtype='int16',
                                                                                        handle_unknown='use_encoded_value',
                                                                                        unknown_value=-1),
                                                                         <sklearn.compose._column_transformer.make_column_selector object at 0x7f5f7f9b1a00>)])),
                                       ('randomforestregressor',
                                        RandomForestRegressor(n_jobs=-1,
                                                              oob_score=True))]),
             n_jobs=-1,
             param_grid={

Посмотрим на результаты.

In [38]:
pd.DataFrame(gs_rf.cv_results_)[[
    'param_randomforestregressor__max_depth',
    'mean_test_score', 'rank_test_score'
]]

param_randomforestregressor__max_depth  mean_test_score  rank_test_score
0                                      5     -2314.203545                3
1                                     10     -1821.096958                2
2                                     15     -1568.274794                1

Занесём результаты в итоговую таблицу.

In [39]:
results = pd.DataFrame(gs_rf.cv_results_)

results_table[gs_rf.best_estimator_.named_steps[gs_rf.best_estimator_.steps[1][0]].__class__.__name__] = [
    results[results['rank_test_score'] == 1]['mean_fit_time'].values[0],
    results[results['rank_test_score'] == 1]['mean_score_time'].values[0],
    abs(results[results['rank_test_score'] == 1]['mean_test_score'].values[0])
]

Далее будем исследовать модели градиентного бустинга.

### Модель GradientBoostingRegressor

Создадим pipeline.

In [40]:
pipe_gb = make_pipeline(
    ensemble_transformer,
    GradientBoostingRegressor(
        random_state=SEED
    )
)

Зададим сетку параметров и создадим estimator.

In [41]:
param_grid = {
    'gradientboostingregressor__learning_rate':[.1, .5],
    'gradientboostingregressor__n_estimators':[400]
}

gs_gb = GridSearchCV(
    pipe_gb,
    param_grid,
    scoring='neg_root_mean_squared_error',
    n_jobs=-1,
    verbose=1
)

Проведём обучение с кросс-валидацией выбранного оценщика.

In [42]:
%time gs_gb.fit(X, y)

Fitting 5 folds for each of 2 candidates, totalling 10 fits
CPU times: user 8min 38s, sys: 0 ns, total: 8min 38s
Wall time: 8min 39s


GridSearchCV(estimator=Pipeline(steps=[('columntransformer',
                                        ColumnTransformer(remainder='passthrough',
                                                          transformers=[('ordinalencoder',
                                                                         OrdinalEncoder(dtype='int16',
                                                                                        handle_unknown='use_encoded_value',
                                                                                        unknown_value=-1),
                                                                         <sklearn.compose._column_transformer.make_column_selector object at 0x7f5f7f9b1a00>)])),
                                       ('gradientboostingregressor',
                                        GradientBoostingRegressor(random_state=314159))]),
             n_jobs=-1,
             param_grid={'gradientboostingregressor__learning_rate': [0.1, 0.5],
    

Посмотрим на результаты.

In [43]:
pd.DataFrame(gs_gb.cv_results_)[[
    'param_gradientboostingregressor__learning_rate',
    'param_gradientboostingregressor__n_estimators',
    'mean_test_score', 'rank_test_score'
]]

param_gradientboostingregressor__learning_rate  \
0                                            0.1   
1                                            0.5   

  param_gradientboostingregressor__n_estimators  mean_test_score  \
0                                           400     -1697.711130   
1                                           400     -1603.238593   

   rank_test_score  
0                2  
1                1

Занесём результаты в итоговую таблицу.

In [44]:
results = pd.DataFrame(gs_gb.cv_results_)

results_table[gs_gb.best_estimator_.named_steps[gs_gb.best_estimator_.steps[1][0]].__class__.__name__] = [
    results[results['rank_test_score'] == 1]['mean_fit_time'].values[0],
    results[results['rank_test_score'] == 1]['mean_score_time'].values[0],
    abs(results[results['rank_test_score'] == 1]['mean_test_score'].values[0])
]

### Библиотека LightGBM

Для работы с библиотекой необходимо перевести все категориальные признаки в целые числа. Воспользуемся определённым ранее трансформером для ансамблей.

In [45]:
cat_labels = ['vehicle_type', 'gearbox', 'model', 'fuel_type', 'brand', 'not_repaired']
num_labels = ['price', 'registration_year', 'power', 'kilometer']
labels = cat_labels + num_labels

In [46]:
df_lgbm = pd.DataFrame(ensemble_transformer.fit_transform(df), columns=labels)

Разделим данные на обучающие и тестовые для features(X) и target(y).

In [47]:
X_lgbm = df_lgbm.drop(['price'], axis=1)
y_lgbm = df_lgbm['price']

X_lgbm, X_lgbm_test, y_lgbm, y_lgbm_test = train_test_split(
    X_lgbm, y_lgbm,
    test_size=.2,
    random_state=SEED
)

Создадим модель.

In [48]:
model = lgb.LGBMRegressor(
    objective='regression',
    metrics='rmse',
    verbosity=-1
)

In [49]:
param_grid = {
    'max_depth':[-1, 10, 20],
    'num_leaves':[10, 31],
    'learning_rate':[.1, .5]
}
              
gs_lgbm = GridSearchCV(
    model,
    param_grid,
    scoring='neg_root_mean_squared_error',
    n_jobs=-1,
    verbose=1
)

In [50]:
%time gs_lgbm.fit(X_lgbm, y_lgbm)

Fitting 5 folds for each of 12 candidates, totalling 60 fits
CPU times: user 2h 5min 48s, sys: 1min 3s, total: 2h 6min 52s
Wall time: 2h 7min 3s


GridSearchCV(estimator=LGBMRegressor(metrics='rmse', objective='regression',
                                     verbosity=-1),
             n_jobs=-1,
             param_grid={'learning_rate': [0.1, 0.5], 'max_depth': [-1, 10, 20],
                         'num_leaves': [10, 31]},
             scoring='neg_root_mean_squared_error', verbose=1)

Посмотрим на результаты.

In [51]:
pd.DataFrame(gs_lgbm.cv_results_)[[
    'param_learning_rate',
    'param_max_depth',
    'param_num_leaves',
    'mean_test_score', 'rank_test_score'
]]

param_learning_rate param_max_depth param_num_leaves  mean_test_score  \
0                  0.1              -1               10     -1769.064685   
1                  0.1              -1               31     -1635.617402   
2                  0.1              10               10     -1769.064685   
3                  0.1              10               31     -1637.212577   
4                  0.1              20               10     -1769.064685   
5                  0.1              20               31     -1635.617402   
6                  0.5              -1               10     -1639.036343   
7                  0.5              -1               31     -1561.821289   
8                  0.5              10               10     -1639.036343   
9                  0.5              10               31     -1564.335850   
10                 0.5              20               10     -1639.036343   
11                 0.5              20               31     -1561.821289   

    rank_test_score  
0                10  
1                 4  
2                10  
3                 6  
4                10  
5                 4  
6                 7  
7                 1  
8                 7  
9                 3  
10                7  
11                1

Занесём результаты в итоговую таблицу.

In [52]:
results = pd.DataFrame(gs_lgbm.cv_results_)

results_table[gs_lgbm.best_estimator_.__class__.__name__] = [
    results[results['rank_test_score'] == 1]['mean_fit_time'].values[0],
    results[results['rank_test_score'] == 1]['mean_score_time'].values[0],
    abs(results[results['rank_test_score'] == 1]['mean_test_score'].values[0])
]

Посмотрим на библиотеку CatBoost.

### Библиотека CatBoost

Создадим модель.

In [53]:
model = CatBoostRegressor(
    iterations=200,
    random_seed=SEED,
    early_stopping_rounds=5,
    cat_features=cat_labels,
    verbose=100
)

Зададим словарь для писка оптимальных гиперпараметров.

In [54]:
param_grid = {
    'learning_rate': [.5],
    'depth': [5, 16]
}
              
gs_cb = GridSearchCV(
    model,
    param_grid,
    scoring='neg_root_mean_squared_error',
    n_jobs=-1,
    cv=3,
    verbose=4
)

Проведём подбор параметров.

In [55]:
%time gs_cb.fit(X, y)

Fitting 3 folds for each of 2 candidates, totalling 6 fits
0:	learn: 3252.8955260	total: 181ms	remaining: 36.1s
100:	learn: 1612.0048484	total: 10.9s	remaining: 10.7s
199:	learn: 1547.4946250	total: 21.3s	remaining: 0us
[CV 1/3] END .....................depth=5, learning_rate=0.5; total time=  22.6s
0:	learn: 3259.5741058	total: 137ms	remaining: 27.2s
100:	learn: 1589.5749976	total: 10.5s	remaining: 10.3s
199:	learn: 1533.9770492	total: 20.9s	remaining: 0us
[CV 2/3] END .....................depth=5, learning_rate=0.5; total time=  22.2s
0:	learn: 3301.4176635	total: 139ms	remaining: 27.6s
100:	learn: 1601.3079189	total: 10.6s	remaining: 10.4s
199:	learn: 1538.4873180	total: 20.6s	remaining: 0us
[CV 3/3] END .....................depth=5, learning_rate=0.5; total time=  21.9s
0:	learn: 2973.3440784	total: 2.03s	remaining: 6m 44s
100:	learn: 1060.6776894	total: 3m 52s	remaining: 3m 47s
199:	learn: 942.7307676	total: 8m 7s	remaining: 0us
[CV 1/3] END ....................depth=16, learning_

GridSearchCV(cv=3,
             estimator=<catboost.core.CatBoostRegressor object at 0x7f5f7e24a3d0>,
             n_jobs=-1, param_grid={'depth': [5, 16], 'learning_rate': [0.5]},
             scoring='neg_root_mean_squared_error', verbose=4)

Посмотрим на результаты.

In [56]:
pd.DataFrame(gs_cb.cv_results_)[[
    'param_learning_rate',
    'param_depth',
    'mean_test_score', 'rank_test_score'
]]

param_learning_rate param_depth  mean_test_score  rank_test_score
0                 0.5           5     -1592.655800                2
1                 0.5          16     -1559.211442                1

Занесём результаты в итоговую таблицу.

In [57]:
results = pd.DataFrame(gs_cb.cv_results_)

results_table[gs_cb.best_estimator_.__class__.__name__] = [
    results[results['rank_test_score'] == 1]['mean_fit_time'].values[0],
    results[results['rank_test_score'] == 1]['mean_score_time'].values[0],
    abs(results[results['rank_test_score'] == 1]['mean_test_score'].values[0])
]

Перейдём к анализу моделей.

## Анализ моделей.

Для каждой модели мы подбирали оптимальные гиперпараметры с целью получения минимальной оценки метрики RMSE. Также мы измеряли время обучения и предсказания моделей, результаты на кросс-валидации.

Посмотрим на сводную таблицу.

In [58]:
pd.DataFrame(
    results_table, index=[
        'fit_time', 'predict_time', 'CV_score'
    ]
).transpose()

fit_time  predict_time     CV_score
DummyRegressor               3.000000      0.500000  4950.000000
LinearRegression            17.382198      0.237768  2553.288151
RandomForestRegressor       29.604324      0.751383  1568.274794
GradientBoostingRegressor   45.314729      0.255409  1603.238593
LGBMRegressor              125.601024      0.339852  1561.821289
CatBoostRegressor          518.906140      0.690536  1559.211442

Все модели, кроме линейной регрессии достигли требуемой точности в 2500 евро (RMSE).

Случайный лес, градиентный бустинг, LightGBM и CatBoost показали схожие результаты по точности, в диапазоне 1550-1600 евро, но при этом в данной задаче LightGBM оказался быстрее всех. Таким образом заказчику рекомендуется использовать для данной задачи модель **LightGBM**.

При этом стоить отметить что модуль CatBoost ощутимо удобнее при использовании и настройке.

Проверим результаты выбранной модели на тестовой выборке.

In [61]:
predictions = gs_lgbm.predict(X_lgbm_test)
rmse = mean_squared_error(y_lgbm_test, predictions, squared=False)
print(f'Метрика RMSE на тестовой выборке для модели LightGBM составила {rmse:.2f} евро.')

Метрика RMSE на тестовой выборке для модели LightGBM составила 1572.61 евро.


## Общий вывод

В данной работе мы изучили и обработали датасет с объявлениями о продаже машин.

  * Загрузили данные и провели EDA.
  * Изучили и удалили дубликаты.
  * Привели датасет в соответствие с нормами PEP8, отбросили неинофрмативные колонки.
  * Обработали и частично заполнили пропуски.
    
Сделали baseline из модели **DummyRegressor** для проверки на адекватность. Изучили ряд моделей. Одну линейную:

  * **LinearRegression** из модуля **sklearn**
  
Две ансамблевых модели из модуля **sklearn**:

  * **RandomForestRegressor**
  * **GradientBoostingRegressor**
  
А также две модели градиентного бустинга из отдельных модулей:

  * **LightGBM** от **Microsoft**
  * **CatBoost** от **Yandex**
  
Для каждой модели мы подбирали оптимальные гиперпараметры с целью получения минимальной оценки метрики RMSE. Также мы измеряли время обучения моделей и время предсказаний, результаты на кросс-валидации. По итогам анализа результатов было принято решение рекомендовать заказчику, по совокупности результатов, модель **LightGBM**.